In [1]:
import pandas as pd

In [2]:
data = pd.read_csv('amazon_reviews_us_Digital_Video_Games_v1_00.tsv',sep = '\t')

In [3]:
data.head(5)

marketplace  customer_id       review_id  product_id  product_parent  \
0          US     21269168   RSH1OZ87OYK92  B013PURRZW       603406193   
1          US       133437  R1WFOQ3N9BO65I  B00F4CEHNK       341969535   
2          US     45765011   R3YOOS71KM5M9  B00DNHLFQA       951665344   
3          US       113118  R3R14UATT3OUFU  B004RMK5QG       395682204   
4          US     22151364   RV2W9SGDNQA2C  B00G9BNLQE       640460561   

                                       product_title     product_category  \
0              Madden NFL 16 - Xbox One Digital Code  Digital_Video_Games   
1                                Xbox Live Gift Card  Digital_Video_Games   
2  Command & Conquer The Ultimate Collection [Ins...  Digital_Video_Games   
3                      Playstation Plus Subscription  Digital_Video_Games   
4  Saints Row IV - Enter The Dominatrix [Online G...  Digital_Video_Games   

   star_rating  helpful_votes  total_votes vine verified_purchase  \
0            2              2            3    N                 N   
1            5              0            0    N                 Y   
2            5              0            0    N                 Y   
3            5              0            0    N                 Y   
4            5              0            0    N                 Y   

                        review_headline  \
0  A slight improvement from last year.   
1                            Five Stars   
2               Hail to the great Yuri!   
3                            Five Stars   
4                            Five Stars   

                                         review_body review_date  
0  I keep buying madden every year hoping they ge...  2015-08-31  
1                                            Awesome  2015-08-31  
2  If you are prepping for the end of the world t...  2015-08-31  
3                                            Perfect  2015-08-31  
4                                           Awesome!  2015-08-31

In [5]:
# install the ydata-profiling package
#%pip install ydata-profiling
# load the ydata_profiling package
from ydata_profiling import ProfileReport
# use ProfileReport
pr_df = ProfileReport(data)
# show pr_df
pr_df


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [18]:
# Drop rows where review_body is NaN
data.dropna(subset=['review_body'], inplace=True)


In [19]:
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer, PorterStemmer
import re
# Load stop words and stemmer
nltk.download('stopwords')
nltk.download('wordnet')
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()
stemmer = PorterStemmer()

# Define preprocessing function
def preprocess_text(text):
    # Convert to lowercase
    text = text.lower()
    
    # Remove punctuation
    text = re.sub(r'[^\w\s]', '', text)
    
    # Tokenize text
    tokens = nltk.word_tokenize(text)
    
    # Remove stop words
    tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatize tokens
    tokens = [lemmatizer.lemmatize(token) for token in tokens]
    
    # Stem tokens
    tokens = [stemmer.stem(token) for token in tokens]
    
    # Join tokens back into a string
    text = ' '.join(tokens)
    
    return text

# Apply preprocessing function to text data
data['review_body'] = data['review_body'].apply(preprocess_text)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\PC2\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\PC2\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [20]:
# Convert star rating to sentiment
data['sentiment'] = data['star_rating'].apply(lambda x: 'positive' if x >= 4 else 'neutral' if x == 3 else 'negative')

In [21]:
from sklearn.preprocessing import LabelEncoder

# Create label encoder
le = LabelEncoder()

# Encode sentiment labels as numerical values
data['sentiment_encoded'] = le.fit_transform(data['sentiment'])


In [23]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from sklearn.feature_extraction.text import TfidfVectorizer

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(data['review_body'], data['sentiment_encoded'], test_size=0.2, random_state=42)
# Vectorize text data using TF-IDF
vectorizer = TfidfVectorizer()
X_train = vectorizer.fit_transform(X_train)
X_test = vectorizer.transform(X_test)
# Train random forest classifier on training data
rfc = RandomForestClassifier()
rfc.fit(X_train, y_train)

# Predict sentiment labels for test data
y_pred = rfc.predict(X_test)

# Calculate accuracy score
accuracy = accuracy_score(y_test, y_pred)
print('Accuracy:', accuracy)


KeyboardInterrupt: 

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, classification_report

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(data['review_body'], data['star_rating'], test_size=0.2, random_state=42)

# Vectorize text data using TF-IDF
vectorizer = TfidfVectorizer()
X_train = vectorizer.fit_transform(X_train)
X_test = vectorizer.transform(X_test)

# Train Naive Bayes classifier
clf = MultinomialNB()
clf.fit(X_train, y_train)

# Predict star rating for test data
y_pred = clf.predict(X_test)

# Evaluate performance
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)
print("Accuracy:", accuracy)
print("Report:", report)


Accuracy: 0.6173777854551736
Report:               precision    recall  f1-score   support

           1       0.84      0.39      0.53      4999
           2       0.00      0.00      0.00      1609
           3       0.78      0.00      0.01      2344
           4       0.60      0.00      0.00      4050
           5       0.60      1.00      0.75     15943

    accuracy                           0.62     28945
   macro avg       0.56      0.28      0.26     28945
weighted avg       0.62      0.62      0.50     28945



c:\Users\PC2\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\PC2\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\PC2\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [ ]:
# Compare predicted labels with ground truth labels
data['predicted_rating'] = clf.predict(vectorizer.transform(data['review_body']))
data['correct_prediction'] = data['predicted_rating'] == data['star_rating']

# Calculate accuracy
accuracy = data['correct_prediction'].mean()
print("Accuracy:", accuracy)


Accuracy: 0.6273268749740882
